In [1]:
import os
import langchain_chroma
import openai
from openai import OpenAI
import chromadb
import fitz  # PDF에서 텍스트 추출
from dotenv import load_dotenv
from fastapi import FastAPI, UploadFile, File
from sqlalchemy import create_engine, text
from sqlalchemy.ext.declarative import declarative_base
import pandas as pd
import psycopg2
import torch
from sklearn.metrics.pairwise import cosine_similarity
from langchain_text_splitters import RecursiveCharacterTextSplitter


# .env 파일 로드
load_dotenv()
OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")
POST_DB_HOST = os.getenv("POST_DB_HOST")
POST_DB_NAME = os.getenv("POST_DB_NAME")
POST_DB_USER = os.getenv("POST_DB_USER")
POST_DB_PASSWD = os.getenv("POST_DB_PASSWD")
POST_DB_PORT = os.getenv("POST_DB_PORT")
# PostgreSQL 연결 엔진 생성
post_engine = create_engine(f'postgresql://{POST_DB_USER}:{POST_DB_PASSWD}@{POST_DB_HOST}:{POST_DB_PORT}/{POST_DB_NAME}')
db = psycopg2.connect(host=POST_DB_HOST, dbname=POST_DB_NAME,user=POST_DB_USER,password=POST_DB_PASSWD,port=POST_DB_PORT)
cursor = db.cursor()
db.autocommit = False

In [2]:
openai_client = OpenAI()

In [3]:
# postgreSQL 에서 데이터 가져오기기
sql = """
        select rec_idx, company_nm, jd_text,recruit_title, recruit_kewdcdnm, company_place, career, education from saramin_recruit_detail
"""

cursor.execute(sql)

In [4]:
jd_list = cursor.fetchall()

In [5]:
db.commit()
cursor.close()
db.close()

In [6]:
# 텍스트 임베딩 함수
def get_embedding(text, model="text-embedding-3-large"):
    response = openai.embeddings.create(
        text = resume_text.replace("\n", "").strip(),
        model=model,
        input=text
    )
    return response.data[0].embedding

임베딩 컬럼 
- jd_text
- recruit_title

meta data
- rec_idx
- company_nm
- recruit_kewdcdnm
- company_place
- career
- education

In [7]:
jd_list

[(50245530,
  '(주)하이로닉',
  '\n채용공고 상세\n[코스닥 상장사] 경영기획본부 신입2007년 12월 11일에 설립된 그 외 기타 의료용 기기 제조업업종의 피부미용 의료기기 제조,중개,무역사업을 하는 코스닥,중소기업,주식회사,외부감사법인,병역특례 인증업체,수출입 기업 입니다.모집부문 및 상세내용모집부문상세내용공통 자격요건ㆍ학력 : 대졸 이상 (4년)ㆍ학점 : 3.8 이상경영기획본부전략기획팀 1명주요업무담당업무ㆍ지원직무주요 회의체 운영 및 경영진 지원 (회의 안건 준비, 회의록 작성 등)조직별 성과 데이터 집계 및 분석, 경영진 보고사업 전략 및 중장기 계획 수립 지원기타 경영지원 및 프로젝트성 업무 수행지원자격데이터 분석 및 보고서 작성 능력 (Excel, PowerPoint 활용)커뮤니케이션 및 조율 역량 보유컨설팅 및 전략 기획 관련 경험 우대\nㆍ기타 필수 사항\n우대사항✅ 전략기획, 경영관리 등 유관 업무 경험 보유자✅ 데이터 분석 및 리포팅 역량 우수자 (BI 툴, SQL 활용 가능자 우대)✅ 사업 전략 및 중장기 계획 수립 경험자✅ 주요 프로젝트 운영 경험 보유자근무조건ㆍ근무형태:정규직(수습기간)-3개월ㆍ근무일시:주 5일(월~금)ㆍ근무지역:(16827) 경기 용인시 수지구 신수로 767 분당수지 U-TOWER 19층(동천동) - 신분당선 동천 에서 200m 이내전형절차 서류전형 1차면접 2차면접(경우에 따라 생략 가능) 최종합격접수기간 및 방법ㆍ:2025년 3월 14일 (금) 14시~ 채용시ㆍ접수방법:사람인 입사지원ㆍ이력서양식:사람인 온라인 이력서ㆍ제출서류:유의사항ㆍ학력, 성별, 연령을 보지않는 블라인드 채용입니다. ㆍ입사지원 서류에 허위사실이 발견될 경우, 채용확정 이후라도 채용이 취소될 수 있습니다.ㆍ모집분야별로 마감일이 상이할 수 있으니 유의하시길 바랍니다.\n',
  '[코스닥 상장사] 경영기획 신입',
  "['경영기획', '전략기획', '경영분석', '경영컨설팅', '사업관리']",
  '경기 용인시 수지구',
  '신

In [8]:
len(jd_list)

13853

In [9]:
df = pd.DataFrame(jd_list, columns=['rec_idx', 'company_nm', 'jd_text','recruit_title', 'recruit_kewdcdnm', 'company_place', 'career', 'education'])

In [10]:
df

rec_idx       company_nm  \
0      50245530          (주)하이로닉   
1      50275785      세일즈웍스코리아(유)   
2      50275903         엔에이치엔(주)   
3      50254512  (주)글로벌스탠다드테크놀로지   
4      49874934      (주)에이치비투자그룹   
...         ...              ...   
13848  50185544            (주)핀다   
13849  50170082        오픈헬스케어(주)   
13850  50090229      (주)두나미스자산운용   
13851  50109575         (주)에코앤드림   
13852  50136151          (사)월드쉐어   

                                                 jd_text  \
0      \n채용공고 상세\n[코스닥 상장사] 경영기획본부 신입2007년 12월 11일에 설...   
1                                            \n채용공고 상세\n   
2      \n채용공고 상세\nNHN  Dooray!올인원 협업 도구 두레이와 전자결재/게시판...   
3      \n채용공고 상세\n모집부문 및 자격요건\n 모집부문\n 경력사항\n 담당업무\n자...   
4                                            \n채용공고 상세\n   
...                                                  ...   
13848  \n채용공고 상세\n 구분\n 상세내용\nBusiness\nPO\n(비교대출)\n(...   
13849  \n채용공고 상세\n\t\n\t 오픈헬스케어(주) ㅣ 전략기획본부 투자팀 - 경력\...   
13850  \n채용공고 상세\n \n (주)두나미스자산운용\n \n펀드마케팅 \n경력3년이상(...   
13851  \n채용공고 상세\n재무기획(FP&A) 담당자 채용\n# 모집부문 \n모집부문\n담...   
13852  \n채용공고 상세\n모집상세\n 모집부문\n 담당업무\n 자격요건 및 우대사항\n ...   

                              recruit_title  \
0                         [코스닥 상장사] 경영기획 신입   
1      [외국계 본사 / 정규직 /복리후생有] 외국계 부문별 신입/경력직   
2                   [NHN Dooray] ERP 서비스 기획   
3                       [GST] 액침냉각 담당 인재 채용   
4      (주)에이치비투자그룹 주식/코인 2025 상반기 영업(TM) 채용   
...                                     ...   
13848                    Business PO (비교대출)   
13849                       전략기획본부 투자팀 - 경력   
13850                 펀드마케팅 경력 3년이상(대리~부장급)   
13851          [코스닥] 재무기획(FP&A) 담당자 채용 - 서울   
13852              모금사업부/필리핀지부장/에티오피아지부장 채용   

                                      recruit_kewdcdnm company_place  \
0            ['경영기획', '전략기획', '경영분석', '경영컨설팅', '사업관리']    경기 용인시 수지구   
1           ['거래처관리', '고객관리', '매장관리', '매출관리', '데이터분석']      서울 강남구 외   
2                                     ['ERP', '서비스기획']    경기 성남시 분당구   
3            ['SAP', '특허명세사', '특허관리', '특허분석', '특허컨설팅']      경기 화성시 외   
4                     ['영업직', '전략기획', '투자전략', '투자자문사']       서울 영등포구   
...                                                ...           ...   
13848  ['사업기획', '서비스기획', 'PO(프로덕트오너)', '사업개발', '사업관리']      서울 강남구 외   
13849         ['투자전략', '투자검토', '투자분석', '투자심사', '투자자문']      서울 성동구 외   
13850    ['마케팅기획', '비즈니스마케팅', '통계/분석', '금융사무', '기업금융']        서울 강남구   
13851           ['세무사', '회계사', '관리회계', '기업회계', '내부감사']      서울 금천구 외   
13852  ['관리회계', '급여(Payroll)', '법인결산', '자금관리', '자산관리']      서울 구로구 외   

                career education  
0             신입 · 정규직  대학교(4년)↑  
1         경력무관 · 정규직 외      학력무관  
2         경력 4년↑ · 정규직      학력무관  
3             경력 · 정규직  대학교(4년)↑  
4           경력무관 · 정규직      학력무관  
...                ...       ...  
13848     4 ~ 7년 · 정규직       고졸↑  
13849     5 ~ 8년 · 정규직  대학교(4년)↑  
13850   경력 3년↑ · 정규직 외  대학교(4년)↑  
13851     경력 5년↑ · 정규직  대학교(4년)↑  
13852  신입 · 경력 · 정규직 외      학력무관  

[13853 rows x 8 columns]

In [11]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [12]:
def get_embedding(text, model="text-embedding-3-small"):
    text = text.replace("\n", " ").strip()
    return openai_client.embeddings.create(input=[text], model=model).data[0].embedding

In [13]:
df['jd_text'] = df['recruit_title'].map(str) + '\n' + df['jd_text'].map(str)

In [14]:
df.drop(columns=['recruit_title'], inplace=True)

In [15]:
# text split 
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=1000,
    chunk_overlap=200
)

In [16]:
chunks = []
metas = []

for _, row in df.iterrows():
    jd_text = row["jd_text"]
    rec_idx = row["rec_idx"]

    split_texts = text_splitter.split_text(jd_text)
    for i, chunk in enumerate(split_texts):
        chunks.append(chunk)

        meta = row.drop("jd_text").to_dict()
        meta["chunk_id"] = f"{rec_idx}_{i}"
        metas.append(meta)

In [17]:
# 1. chunk들을 rec_idx 기준으로 합치기
chunk_df = pd.DataFrame({
    "rec_idx": [meta["rec_idx"] for meta in metas],
    "chunk": chunks
})

grouped_text = chunk_df.groupby("rec_idx")["chunk"].apply(lambda x: " ".join(x)).reset_index()

# 2. 첫 번째 메타데이터만 추출
meta_df = pd.DataFrame(metas).drop(columns=["chunk_id"])
meta_df = meta_df.groupby("rec_idx").first().reset_index()

# 3. 병합
final_df = pd.merge(grouped_text, meta_df, on="rec_idx")

In [139]:
final_df.to_csv("../data_backup/rec_data.csv")

In [20]:
from tqdm import tqdm

embeddings = [get_embedding(chunk) for chunk in tqdm(chunks)]

100%|██████████| 21806/21806 [3:05:41<00:00,  1.96it/s]   


In [22]:
import pickle

# 피클 형식 (빠르고 이진 저장)
with open("../data_backup/recruit_embeddings.pkl", "wb") as f:
    pickle.dump(embeddings, f)

# 일단 embedding 

# chroma에 적재

In [26]:
chroma_client = chromadb.HttpClient(host='43.202.186.183 ', port=8000)  # 원하는 경로로 지정 가능
collection_name = "chroma_rec"

ValueError: Could not connect to a Chroma server. Are you sure it is running?

In [ ]:
# ChromaDB 적재
for _, row in tqdm(final_df.iterrows(), total=len(final_df)):
    text = row["chunk"]
    embedding = get_embedding(text)

    metadata = row.drop(["chunk"]).to_dict()

    collection.add(
        documents=[text],
        embeddings=[embedding],
        metadatas=[metadata],
        ids=[str(row["rec_idx"])]
    )

In [135]:
chroma_client = chromadb.Client()
collection_name = 'chroma_test'
try:
    collection = chroma_client.get_collection(name=collection_name,
                                              metadata={"hnsw:space": "cosion"})
except:
    collection = chroma_client.create_collection(name=collection_name)

UniqueConstraintError: Collection chroma_test already exists

In [ ]:
# Chroma 적재
collection.add(
    documents=chunks,
    embeddings=embeddings,
    metadatas=metas,
    ids=[meta["chunk_id"] for meta in metas],
)
print(f"{len(chunks)}")

TypeError: Collection.add() got an unexpected keyword argument 'collection_metadata'

In [54]:
metas

[{'rec_idx': 50245530,
  'company_nm': '(주)하이로닉',
  'recruit_kewdcdnm': "['경영기획', '전략기획', '경영분석', '경영컨설팅', '사업관리']",
  'company_place': '경기 용인시 수지구',
  'career': '신입 · 정규직',
  'education': '대학교(4년)↑',
  'chunk_id': '50245530_0'},
 {'rec_idx': 50275785,
  'company_nm': '세일즈웍스코리아(유)',
  'recruit_kewdcdnm': "['거래처관리', '고객관리', '매장관리', '매출관리', '데이터분석']",
  'company_place': '서울 강남구 외',
  'career': '경력무관 · 정규직 외',
  'education': '학력무관',
  'chunk_id': '50275785_0'},
 {'rec_idx': 50275903,
  'company_nm': '엔에이치엔(주)',
  'recruit_kewdcdnm': "['ERP', '서비스기획']",
  'company_place': '경기 성남시 분당구',
  'career': '경력 4년↑ · 정규직',
  'education': '학력무관',
  'chunk_id': '50275903_0'},
 {'rec_idx': 50275903,
  'company_nm': '엔에이치엔(주)',
  'recruit_kewdcdnm': "['ERP', '서비스기획']",
  'company_place': '경기 성남시 분당구',
  'career': '경력 4년↑ · 정규직',
  'education': '학력무관',
  'chunk_id': '50275903_1'},
 {'rec_idx': 50275903,
  'company_nm': '엔에이치엔(주)',
  'recruit_kewdcdnm': "['ERP', '서비스기획']",
  'company_place': '경기 성남시 분당구',

In [50]:
# Chroma 내부 전체 데이터 확인
data = collection.get(include=["documents", "metadatas"])

for i, (doc, meta) in enumerate(zip(data["documents"], data["metadatas"])):
    print(f"[{i}] rec_idx: {meta['rec_idx']}, chunk_id: {meta['chunk_id']}")
    print(f"   ▶ {doc[:100]}...\n")

[0] rec_idx: 50245530, chunk_id: 50245530_0
   ▶ [코스닥 상장사] 경영기획 신입

채용공고 상세
[코스닥 상장사] 경영기획본부 신입2007년 12월 11일에 설립된 그 외 기타 의료용 기기 제조업업종의 피부미용 의료기기 제조,중...

[1] rec_idx: 50275785, chunk_id: 50275785_0
   ▶ [외국계 본사 / 정규직 /복리후생有] 외국계 부문별 신입/경력직

채용공고 상세...

[2] rec_idx: 50275903, chunk_id: 50275903_0
   ▶ [NHN Dooray] ERP 서비스 기획...

[3] rec_idx: 50275903, chunk_id: 50275903_1
   ▶ 채용공고 상세...

[4] rec_idx: 50275903, chunk_id: 50275903_2
   ▶ NHN  Dooray!올인원 협업 도구 두레이와 전자결재/게시판을 통합한 그룹웨어, 인사/재무 서비스를 제공하는 ERP로 통합한 협업 플랫폼입니다. 공공기관과 주요 대학을 비롯하여...

[5] rec_idx: 50275903, chunk_id: 50275903_3
   ▶ (주요 업무) · 대내외 ERP 서비스 기획/운영 (프로덕트 매니저) 이런 분들을 찾고 있어요 (자격 요건)· 재무제표 및 결산 업무에 대한 이해가 있으신 분· ERP 서비스 기획...

[6] rec_idx: 50275903, chunk_id: 50275903_4
   ▶ 합니다. · 제출서류나 각종 증명서의 기재내용이 허위일 경우, 응시를 무효로 하며 합격을 취소합니다. · 근무지는 판교 삼평동 플레이뮤지엄(Play Museum)입니다.· 가지고 ...

[7] rec_idx: 50254512, chunk_id: 50254512_0
   ▶ [GST] 액침냉각 담당 인재 채용

채용공고 상세
모집부문 및 자격요건
 모집부문
 경력사항
 담당업무
자격요건 및 우대사항
냉각시스템
기획/전략 담당자
과장급 모집

(기획

# elastic search 적재

In [ ]:
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk
es_client = Elasticsearch('')

In [ ]:
actions = [
    {
        "_index": index_name,
        "_id": str(row["rec_idx"]),
        "_source": {
            **row.drop(["chunk"]).to_dict(),
            "description": row["chunk"]
        }
    }
    for _, row in final_df.iterrows()
]

In [ ]:
helpers.bulk(es_client, actions)

# local에서 테스트 

In [128]:
# 이력서 불러오기
path = "./data/빅데이터AI_이력서.pdf"
doc = fitz.open(path)
for page in doc:
    resume_text = page.get_text()
    print(resume_text)

📄 이력서 (Resume)
[기본 정보]
이름: 홍길동
연락처: 010-1234-5678
이메일: honggildong.ai@gmail.com
주소: 서울특별시 강남구 테헤란로 123
[학력]
고려대학교 컴퓨터학과 졸업 (2018.03 ~ 2024.02)
GPA: 3.85 / 4.5
관련 과목: 머신러닝, 데이터마이닝, 통계학, 빅데이터처리, 딥러닝 이론과 실습
[기술 스택]
Programming: Python, SQL, R
Frameworks/Libraries: Scikit-learn, TensorFlow, PyTorch, Pandas, NumPy
Tools: Jupyter, Git, Docker, Tableau
DBMS: MySQL, MongoDB, Hadoop(HDFS), Spark
Cloud: Google Colab, AWS EC2 & S3 (기초 수준)
[프로젝트 경험]
1. 신문 기사 기반 감성 분석 모델 개발 (2023.03 ~ 2023.06)
자연어처리(NLP) 기반 감성 분류 모델 개발
KoNLPy와 Scikit-learn을 이용한 전처리 및 모델 학습
정확도 86% 달성
2. 머신러닝 기반 개인 맞춤형 영화 추천 시스템 (2023.09 ~ 2023.12)
📄 이력서 (Resume)
1

Content-based Filtering 및 Collaborative Filtering 기법 적용
Streamlit으로 웹 인터페이스 구현
kaggle 데이터셋 기반, Precision@10: 0.73
[자격증]
ADsP (데이터분석 준전문가) – 2023.08
SQLD (SQL 개발자) – 2024.01
📄 이력서 (Resume)
2



In [129]:
query = resume_text

In [21]:
import time
from elasticsearch import Elasticsearch
from chromadb import Client
from openai import OpenAI

In [30]:
openai_client = OpenAI()

In [ ]:
data = collection.get(include=["documents", "metadatas"], limit=5)

for doc, meta in zip(data["documents"], data["metadatas"]):
    print(f"[{meta['rec_id']} - {meta['company_name']}]\n{doc[:300]}...\n")

In [33]:
chroma_client.heartbeat()

1744355051346860710

# 일반 LLM

In [130]:
# 일반 LLM 모델

load_dotenv()
client = OpenAI()

def generate_job_recommendation(resume_text: str, user_prompt: str) -> str:
    messages = [
        {
            "role": "system",
            "content": "당신은 이력서 추천천 AI입니다. 사용자의 이력서를 기반으로 적합한 채용 공고를 추천해 주세요.",
        },
        {
            "role": "user",
            "content": f"""[이력서]
{resume_text}

[요청]
{user_prompt}
""",
        }
    ]

    try:
        completion = client.chat.completions.create(
            model="gpt-4o",
            messages=messages,
            temperature=0.7,
            max_tokens=1000,
        )
        return completion.choices[0].message.content.strip()
    except Exception as e:
        return f"{e}"

# 예시 실행
if __name__ == "__main__":
    resume = resume_text

    prompt = "이 이력서를 바탕으로 적합한 채용 공고 5개를 추천해 주세요."

    result = generate_job_recommendation(resume, prompt)
    print(result)


이 이력서를 기반으로 추천할 수 있는 채용 공고는 다음과 같습니다:

1. **데이터 사이언티스트**
   - 역할: 추천 시스템 개발 및 최적화
   - 요구 조건: Content-based Filtering 및 Collaborative Filtering 경험, Python 및 데이터 분석 도구 숙련도
   - 우대 사항: ADsP, SQLD 자격증 소지자

2. **머신러닝 엔지니어**
   - 역할: 머신러닝 모델 개발 및 배포, 대규모 데이터셋 처리
   - 요구 조건: Streamlit 등 웹 인터페이스 구현 경험, 데이터셋 기반 모델 평가 (e.g., Precision@10) 경험
   - 우대 사항: Kaggle 프로젝트 경험

3. **데이터 분석가**
   - 역할: 데이터 분석 및 인사이트 도출
   - 요구 조건: SQL 및 데이터베이스 쿼리 능력, 데이터 시각화 도구 사용 경험
   - 우대 사항: ADsP 자격증 소지자

4. **추천 시스템 엔지니어**
   - 역할: 추천 알고리즘 개발 및 사용자 경험 개선
   - 요구 조건: Content-based 및 Collaborative Filtering 관련 프로젝트 경험, Python 및 데이터 처리 라이브러리 숙련도
   - 우대 사항: 데이터 분석 관련 자격증

5. **웹 애플리케이션 개발자 (데이터 중심)**
   - 역할: 데이터 기반 웹 애플리케이션 개발 및 유지보수
   - 요구 조건: Streamlit 및 유사한 프레임워크 경험, 데이터 분석 및 처리 능력
   - 우대 사항: 데이터 분석 프로젝트 경험, SQLD 자격증 소지자

이 목록은 귀하의 기술 및 자격증을 기반으로 한 추천이며, 구체적인 채용 공고를 확인하기 위해 해당 직무와 연관된 회사의 채용 페이지를 방문하시기 바랍니다.


# chroma RAG

In [132]:
recommendations = recommend_jobs_from_resume_text(
    resume_text=resume_text,
    collection=collection,
    top_k=5
)

In [133]:
for i, rec in enumerate(recommendations, 1):
    jd = rec.get("JD 내용") or "(JD 내용 없음)"

    print(f"\n[{i}] {rec['회사명']} (공고 ID: {rec['공고ID']})")
    print(f"위치: {rec['근무지']} | 경력: {rec['경력']} | 학력: {rec['학력']}")
    print(f"유사도 점수: {rec['유사도 점수']}")
    print(f"채용공고:\n{jd[:800]}...")


[1] (주)엘지씨엔에스 (공고 ID: 50226095)
위치: 서울 강서구 외 | 경력: 신입 · 정규직 | 학력: 대학교(4년)↑
유사도 점수: 1.0225
채용공고:
IT개발·데이터 > 직무·직업 > IT컨설팅
IT개발·데이터 > 직무·직업 > QA/테스터
IT개발·데이터 > 직무·직업 > SE(시스템엔지니어)
IT개발·데이터 > 직무·직업 > SI개발
IT개발·데이터 > 직무·직업 > SQA
IT개발·데이터 > 전문분야 > 검색엔진
IT개발·데이터 > 전문분야 > 네트워크
IT개발·데이터 > 전문분야 > 데이터라벨링
IT개발·데이터 > 전문분야 > 데이터마이닝
IT개발·데이터 > 전문분야 > 데이터시각화
IT개발·데이터 > 전문분야 > 딥러닝
IT개발·데이터 > 전문분야 > 머신러닝
IT개발·데이터 > 전문분야 > 메타버스
IT개발·데이터 > 전문분야 > 모델링
IT개발·데이터 > 전문분야 > 모의해킹
IT개발·데이터 > 전문분야 > 미들웨어
IT개발·데이터 > 전문분야 > 반응형웹
IT개발·데이터 > 전문분야 > 방화벽
IT개발·데이터 > 전문분야 > 블록체인
IT개발·데이터 > 전문분야 > 빅데이터
IT개발·데이터 > 전문분야 > 빌링
IT개발·데이터 > 전문분야 > 솔루션
IT개발·데이터 > 전문분야 > 스크립트
IT개발·데이터 > 전문분야 > 신경망
IT개발·데이터 > 전문분야 > 아키텍쳐
IT개발·데이터 > 전문분야 > 악성코드
IT개발·데이터 > 전문분야 > 알고리즘
IT개발·데이터 > 전문분야 > 임베디드
IT개발·데이터 > 전문분야 > 정보통신
IT개발·데이터 > 전문분야 > 챗봇
IT개발·데이터 > 전문분야 > 클라우드
IT개발·데이터 > 전문분야 > 텍스트마이닝
IT개발·데이터 > 전문분야 > 트러블슈팅
IT개발·데이터 > 전문분야 > 펌웨어
IT개발·...

[2] (주)다우기술 (공고 ID: 50178806)
위치: 경기 성남시 외 | 경력: 신입 · 경력 · 정규직 | 학력: 대학(2,3년)↑
유사도 점수: 1.0304
채용공고

# 하이브리드 RAG

In [85]:
from elasticsearch import Elasticsearch
from collections import OrderedDict

In [120]:
# 로컬 ES 서버일 경우
es = Elasticsearch("http://localhost:9200")

# 접속 확인
if es.ping():
    print("Elasticsearch 연결 성공")
else:
    print("Elasticsearch 연결 실패")

Elasticsearch 연결 성공


In [96]:
# Elasticsearch에서 "rec_idx"를 ID로 지정한 매핑
mapping = {
    "mappings": {
        "properties": {
            "company_nm": {"type": "text"},
            "recruit_title": {"type": "text"},
            "recruit_kwdcdnm": {"type": "text"},
            "company_place": {"type": "text"},
            "career": {"type": "text"},
            "education": {"type": "text"},
            "jd_text": {"type": "text"}
        }
    }
}

# 인덱스가 없다면 "jd_index" 인덱스를 생성
es.indices.create(index="jd_index", body=mapping, ignore=400)  # ignore=400은 이미 존재할 경우 무시하는 옵션


/tmp/ipykernel_104568/1761103906.py:17: DeprecationWarning: Passing transport options in the API method is deprecated. Use 'Elasticsearch.options()' instead.
  es.indices.create(index="jd_index", body=mapping, ignore=400)  # ignore=400은 이미 존재할 경우 무시하는 옵션


ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'jd_index'})

In [97]:
from elasticsearch.helpers import bulk

def index_jds_to_es_with_rec_idx(es_client, index_name, metas):
    """
    Chroma에서 쓰던 meta 데이터들을 rec_idx를 ID로 Elasticsearch에 적재
    """
    actions = []
    for meta in metas:
        actions.append({
            "_op_type": "index",  # 이미 존재하는 문서는 덮어쓰기
            "_index": index_name,
            "_id": meta["rec_idx"],  # rec_idx를 ID로 사용
            "_source": {
                "company_nm": meta.get("company_nm"),
                "recruit_title": meta.get("recruit_title"),
                "recruit_kwdcdnm": meta.get("recruit_kwdcdnm"),
                "company_place": meta.get("company_place"),
                "career": meta.get("career"),
                "education": meta.get("education"),
                "jd_text": meta.get("jd_text", ""),
            }
        })

    bulk(es_client, actions)
    print(f"✅ {len(actions)}건 Elasticsearch에 적재 완료")


In [98]:
index_jds_to_es_with_rec_idx(es, "jd_index", metas)


✅ 21806건 Elasticsearch에 적재 완료


In [99]:
def search_job_by_rec_idx(es_client, index_name, rec_idx):
    """
    rec_idx로 JD 검색
    """
    res = es_client.get(index=index_name, id=rec_idx)
    return res["_source"] if res["found"] else None


In [100]:
job = search_job_by_rec_idx(es, "jd_index", rec_idx="50245530")
if job:
    print(f"회사명: {job['company_nm']}")
    print(f"공고 제목: {job['recruit_title']}")
    print(f"JD 내용: {job['jd_text'][:500]}...")  # JD 내용 요약
else:
    print("해당 rec_idx에 대한 채용공고를 찾을 수 없습니다.")


회사명: (주)하이로닉
공고 제목: None
JD 내용: ...


In [102]:
from elasticsearch import Elasticsearch
from collections import OrderedDict

def hybrid_recommendation(
    resume_text,
    chroma_collection,
    es_client: Elasticsearch,
    es_index: str,
    get_embedding_fn,
    top_k_vector=5,
    top_k_keyword=5
):

    # 1. 벡터 임베딩 기반 검색 (Chroma)
    vector = get_embedding_fn(resume_text)
    vector_result = chroma_collection.query(
        query_embeddings=[vector],
        n_results=top_k_vector,
        include=["metadatas", "documents", "distances"]
    )

    vector_items = []
    for meta, doc, score in zip(
        vector_result["metadatas"][0],
        vector_result["documents"][0],
        vector_result["distances"][0]
    ):
        vector_items.append({
            "rec_idx": meta["rec_idx"],
            "source": "chroma",
            "score": 1 - score,  # distance → 유사도 점수
            "meta": meta,
            "jd_text": meta.get("jd_text") or doc.strip(),
        })

    # 2. 키워드 기반 검색 (Elasticsearch)
    es_query = {
        "query": {
            "match": {
                "jd_text": resume_text
            }
        },
        "size": top_k_keyword
    }

    keyword_items = []
    res = es_client.search(index=es_index, body=es_query)
    for hit in res["hits"]["hits"]:
        src = hit["_source"]
        keyword_items.append({
            "rec_idx": src["rec_idx"],
            "source": "elasticsearch",
            "score": hit["_score"] / 100,  # 정규화 (0~1)
            "meta": src,
            "jd_text": src.get("jd_text", "")
        })

    # 3. 결과 통합: rec_idx 기준 중복 제거
    combined = vector_items + keyword_items
    combined_by_idx = OrderedDict()
    for item in sorted(combined, key=lambda x: -x["score"]):
        if item["rec_idx"] not in combined_by_idx:
            combined_by_idx[item["rec_idx"]] = item

    return list(combined_by_idx.values())


In [107]:
for i, rec in enumerate(results, 1):
    m = rec.get("meta", {})
    jd_text = rec.get("jd_text", "").strip()
    
    print(f"\n[{i}] {m.get('company_nm', '[회사명 없음]')} (rec_idx: {rec.get('rec_idx', '-')})")
    print(f"키워드: {m.get('recruit_kwdcdnm', '-')}")
    print(f"위치: {m.get('company_place', '-')}")
    print(f"채용공고 내용:\n{jd_text}" if jd_text else "JD 내용 없음")
    print(f"점수: {rec.get('score', 0):.4f} / 출처: {rec.get('source', '-')}")



[1] 주식회사 다인 (rec_idx: 50018150)
키워드: -
위치: 서울 강남구
채용공고 내용:
노션 활용 능력이 우수하신 분ㆍ인스타그램, 유튜브 등 콘텐츠 제작 및 관리 경험이 있으신 분근무조건ㆍ근무형태:정규직 - 수습 3개월ㆍ근무일시:주 5일(월~금) 09:00~18:00 / 시차출퇴근제 운영ㆍ근무지역:(06242) 서울 강남구 역삼로1길 8 넛지캠퍼스 빌딩(역삼동) - 신분당선 강남 에서 500m 이내접수기간 및 방법ㆍ접수기간:채용시 마감ㆍ접수방법:사람인 입사지원 or 홈페이지 직접지원 [바로가기]ㆍ이력서양식:자유양식ㆍ제출서류:복리후생ㆍ식대 및 복지포인트 제공ㆍ1층 임직원용 카페테리아 운영 (전 메뉴 50% 무제한 할인)ㆍ강남 유명 피부과 제휴 (모든 시술 50% 할인, 제품 30%할인)ㆍ사내 스낵바 운영 (음료와 간식 365일 무한 제공)ㆍ시차출퇴근제 운영 (8시~10시)ㆍ생일 당일 선물 선택 및 오후 반차 제공ㆍEAP상담비용 지원ㆍ장기근속자 포상 Refresh 휴가 지급 (3년, 5년, 7년)ㆍ본인 및 배우자 대상 프리미엄 건강검진 운영ㆍ경조사 지원ㆍ모집분야별로 마감일이 상이할 수 있으니 유의하시길 바랍니다.유의사항ㆍ입사지원 서류에 허위사실이 발견될 경우, 채용확정 이후라도 채용이 취소될 수 있습니다.
점수: 0.0602 / 출처: chroma

[2] 제이비축제연구소 (rec_idx: 50218971)
키워드: -
위치: 서울 광진구
채용공고 내용:
관광 축제, 공연, 전시, 박람회 기획 연출 감독

채용공고 상세
관광 축제, 공연, 전시, 박람회 기획 연출 감독공연 기획업업종의 기획,연구개발,연출,임대제작,창작,예술 서비스/학술연구용역,연구개발/지자체사업 컨설팅,시장,여론조사,광고사업을 하는 중소기업,연구소기업 입니다.모집부문 및 상세내용모집부문상세내용공통 자격요건ㆍ학력 : 대졸 이상 (2,3년)공연기획 0명주요업무ㆍ 문화 예술 프로그램 기획 및 운영ㆍ 마케팅 전략 수립 및 실행ㆍ 이벤트 기획 및 진행ㆍ 공연 홍보 및 프로모션ㆍ 창작물 

# hybrid search ver.2

In [123]:
def hybrid_recommendation2(
    resume_text,
    chroma_collection,
    es_client: Elasticsearch,
    es_index: str,
    get_embedding_fn,
    top_k_vector=5,
    top_k_keyword=5,
    w_chroma=0.9,
    w_es=0.3
):
    vector = get_embedding_fn(resume_text)
    vector_result = chroma_collection.query(
        query_embeddings=[vector],
        n_results=top_k_vector,
        include=["metadatas", "documents", "distances"]
    )

    vector_items = []
    for meta, doc, score in zip(
        vector_result["metadatas"][0],
        vector_result["documents"][0],
        vector_result["distances"][0]
    ):
        sim_score = 1 - score
        vector_items.append({
            "rec_idx": meta["rec_idx"],
            "source": "chroma",
            "score": w_chroma * sim_score,
            "meta": meta,
            "jd_text": meta.get("jd_text") or doc.strip(),
        })

    es_query = {
        "query": {
            "match": {
                "jd_text": resume_text
            }
        },
        "size": top_k_keyword
    }

    keyword_items = []
    res = es_client.search(index=es_index, body=es_query)
    for hit in res["hits"]["hits"]:
        src = hit["_source"]
        keyword_items.append({
            "rec_idx": src["rec_idx"],
            "source": "elasticsearch",
            "score": w_es * (hit["_score"] / 100),  # 가중치 반영
            "meta": src,
            "jd_text": src.get("jd_text", "")
        })

    combined = vector_items + keyword_items
    combined_by_idx = OrderedDict()
    for item in sorted(combined, key=lambda x: -x["score"]):
        if item["rec_idx"] not in combined_by_idx:
            combined_by_idx[item["rec_idx"]] = item

    return list(combined_by_idx.values())


In [124]:
results = hybrid_recommendation2(
    resume_text=resume_text,
    chroma_collection=collection,
    es_client=es,
    es_index="jd_index",
    get_embedding_fn=lambda t: get_embedding(t, model="text-embedding-3-small"),
    top_k_vector=5,
    top_k_keyword=5,
    w_chroma=0.9,
    w_es=0.1
)

In [125]:
for i, rec in enumerate(results, 1):
    meta = rec.get("meta", {})
    print(f"\n[{i}] {meta.get('company_nm', '[회사명 없음]')} (rec_idx: {rec['rec_idx']})")
    print(f"키워드: {meta.get('recruit_kewdcdnm', '-')}")
    print(f"위치: {meta.get('company_place', '-')} | 경력: {meta.get('career', '-')} | 학력: {meta.get('education', '-')}")
    print(f"유사도 점수: {rec['score']:.4f} | 출처: {rec['source']}")
    print(f"상세 요강:\n{rec['jd_text']}...\n")


[1] 주식회사 다인 (rec_idx: 50018150)
키워드: ['인사교육', '교육기획', '교육컨설턴트', '교육운영', '교육컨텐츠개발']
위치: 서울 강남구 | 경력: 경력 1년↑ · 정규직 | 학력: 대학교(4년)↑
유사도 점수: 0.0550 | 출처: chroma
상세 요강:
노션 활용 능력이 우수하신 분ㆍ인스타그램, 유튜브 등 콘텐츠 제작 및 관리 경험이 있으신 분근무조건ㆍ근무형태:정규직 - 수습 3개월ㆍ근무일시:주 5일(월~금) 09:00~18:00 / 시차출퇴근제 운영ㆍ근무지역:(06242) 서울 강남구 역삼로1길 8 넛지캠퍼스 빌딩(역삼동) - 신분당선 강남 에서 500m 이내접수기간 및 방법ㆍ접수기간:채용시 마감ㆍ접수방법:사람인 입사지원 or 홈페이지 직접지원 [바로가기]ㆍ이력서양식:자유양식ㆍ제출서류:복리후생ㆍ식대 및 복지포인트 제공ㆍ1층 임직원용 카페테리아 운영 (전 메뉴 50% 무제한 할인)ㆍ강남 유명 피부과 제휴 (모든 시술 50% 할인, 제품 30%할인)ㆍ사내 스낵바 운영 (음료와 간식 365일 무한 제공)ㆍ시차출퇴근제 운영 (8시~10시)ㆍ생일 당일 선물 선택 및 오후 반차 제공ㆍEAP상담비용 지원ㆍ장기근속자 포상 Refresh 휴가 지급 (3년, 5년, 7년)ㆍ본인 및 배우자 대상 프리미엄 건강검진 운영ㆍ경조사 지원ㆍ모집분야별로 마감일이 상이할 수 있으니 유의하시길 바랍니다.유의사항ㆍ입사지원 서류에 허위사실이 발견될 경우, 채용확정 이후라도 채용이 취소될 수 있습니다....


[2] 제이비축제연구소 (rec_idx: 50218971)
키워드: ['공연기획', '공연예술', '마케팅기획', '마케팅전략', '광고마케팅']
위치: 서울 광진구 | 경력: 경력무관 · 정규직 | 학력: 대학(2,3년)↑
유사도 점수: 0.0514 | 출처: chroma
상세 요강:
관광 축제, 공연, 전시, 박람회 기획 연출 감독

채용공고 상세
관광 축제, 공연, 전시, 박람회 기획 연출 감독공연 기획업업종의 기획,연구개발,연출,임대제작,창작,